In [14]:
%matplotlib notebook

import pandas
from pandas_dedupe import dedupe_dataframe

from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()

import seaborn
seaborn.set(color_codes=True)

import matplotlib
import matplotlib.pyplot as plt

import plotly.express as px

In [15]:
# load all example data into one dataframe
dfs = []
dfs.append(pandas.read_csv('dumps/113.csv', parse_dates=['date']))
dfs.append(pandas.read_csv('dumps/114.csv', parse_dates=['date']))
dfs.append(pandas.read_csv('dumps/115.csv', parse_dates=['date']))
dfs.append(pandas.read_csv('dumps/116.csv', parse_dates=['date']))
df = pandas.concat(dfs)
df.count()

id                 31934
mensa_id           31934
date               31934
name               31934
category           31934
prices_students    29125
notes              31934
dtype: int64

In [16]:
# add day of week column
df['day'] = pandas.to_datetime(df['date']).dt.weekday_name

In [17]:
# replace written numbers in menues
numbers = ["null", "eins", "zwei", "drei", "vier", "fünf", "sechs", "sieben", "acht", "neun"] + [str(i) for i in range(0,10)]

names = df.name
for num in numbers:
    names = names.str.replace(num, "", case=False)

df["name"] = names.astype(str)

In [18]:
# replace old menu names
aliases = [
    ("Menü", "Menü 1"), 
    ("Menü vegetarisch", "Menü 2 vegetarisch"), 
    ("Vital Linie", "Vital-Linie"),
    ("Menü 3", "Vital-Linie"),
    ("Wochenhit/Pastateller", "Wochenhit"),
    ("Menü I", "Menü 1"), 
    ("Menü II vegetarisch", "Menü 2 vegetarisch"), 
    ("Menü III", "Menü 3"), 
]

for old, alias in aliases:
    df.loc[df['category'] == old, ['category']] = alias

In [19]:
# create short names for better grouping 
shortnames = df.name

for word in ["mit", "in", "an", "vom", "aus", "und", "auf", "dazu", "im"]:
    shortnames = shortnames.str.split(f" {word} ", expand=True)[0]

df["sname"] = shortnames.astype(str)

In [20]:
# remove menus with wrong prices (small number)
df = df[df['prices_students'] < 10]

In [21]:
df.sort_values("date").head(10)

id  mensa_id       date  \
30  166411       113 2012-09-03   
47  171112       115 2012-09-03   
46  171113       115 2012-09-03   
45  171115       115 2012-09-03   
44  171114       115 2012-09-03   
21  172584       116 2012-09-03   
32  165320       114 2012-09-03   
31  165321       114 2012-09-03   
30  165322       114 2012-09-03   
20  172585       116 2012-09-03   

                                                 name                category  \
30        Asiatische Gemüsepilzpfanne mit Sojawürfeln      Menü 2 vegetarisch   
47  Putenbrust mit Rahmsauce mit Kartoffelkrokette...    Fleischgericht Abend   
46  Champiognköpfe in Gemüserahmsauce mit Butterre...        Fleischlos Abend   
45               Entenbrust rosa gebraten à la orange  Bistro Gourmet Fleisch   
44                      Rotbarschfilet mit Dillstippe    Bistro Gourmet Fisch   
21  Geröstete Putenbruststreifen "türkische Art" m...                  Menü 1   
32  Geröstete Putenbruststreifen "türkische Art" m...                  Menü 1   
31       Bunter Salatteller mit Käse, Schinken und Ei            Tagesgericht   
30        Asiatische Gemüsepilzpfanne mit Sojawürfeln      Menü 2 vegetarisch   
20  Asiatische Pilzpfanne mit Glasnudeln und Sojaw...      Menü 2 vegetarisch   

    prices_students                                              notes  \
30             2.85  ['mit Konservierungsstoff', 'mit  Antioxidatio...   
47             3.05                                                 []   
46             2.75                                    ['mit Alkohol']   
45             5.35                                                 []   
44             4.45                                                 []   
21             2.85                                                 []   
32             2.85  ['mit Konservierungsstoff', 'mit Geschmacksver...   
31             2.45  ['mit Konservierungsstoff', 'mit Schweinefleis...   
30             2.85  ['mit Konservierungsstoff', 'mit  Antioxidatio...   
20             2.85  ['mit Konservierungsstoff', 'mit Geschmacksver...   

       day                                         sname  
30  Monday                   Asiatische Gemüsepilzpfanne  
47  Monday                                    Putenbrust  
46  Monday                                Champiognköpfe  
45  Monday          Entenbrust rosa gebraten à la orange  
44  Monday                                Rotbarschfilet  
21  Monday  Geröstete Putenbruststreifen "türkische Art"  
32  Monday  Geröstete Putenbruststreifen "türkische Art"  
31  Monday                            Bunter Salatteller  
30  Monday                   Asiatische Gemüsepilzpfanne  
20  Monday                         Asiatische Pilzpfanne

In [22]:
# Second Glimpse: What are the most common meals
meal_occurences = df.groupby("sname").size().sort_values(ascending=False).reset_index(name='count')

fig = px.bar(meal_occurences.head(50), 
             y="sname", 
             x="count", 
             orientation = 'h',
             width=800, 
             height=1000,
             )
fig.show()

In [23]:
# create combined column 
df["mensa_category"] = df["mensa_id"].map(str) + ". " + df["category"]
categories = df.groupby("mensa_category").agg({
    "id": "size", 
    "date": lambda d: d.astype('datetime64[ns]').quantile(.5),
    "prices_students": 'mean',
})
categories.sort_values(by='prices_students').head(20)

id                date  prices_students
mensa_category                                                          
116. Tagesgericht               135 2013-07-12 00:00:00         2.042593
113. Tagesgericht              1746 2016-04-25 12:00:00         2.131300
114. Tagesgericht              1753 2016-05-04 00:00:00         2.132801
115. Tagesgericht               199 2016-05-21 00:00:00         2.168090
115. Menü 3                       1 2019-05-21 00:00:00         2.300000
113. Wochenhit                  274 2015-02-07 12:00:00         2.719891
114. Wochenhit                  164 2014-05-06 12:00:00         2.729573
116. Wochenhit                    1 2017-09-26 00:00:00         2.750000
115. Fleischlos Abend           513 2013-09-24 00:00:00         2.796881
113. Late Lunch vegetarisch       8 2016-05-29 00:00:00         2.825000
114. Late Lunch vegetarisch       6 2016-11-22 12:00:00         2.833333
116. Menü 2 vegetarisch        1528 2016-05-18 12:00:00         2.918488
113. Menü 2 vegetarisch        1708 2016-05-18 12:00:00         2.921516
114. Menü 2 vegetarisch        1707 2016-05-31 00:00:00         2.923433
115. Wochenhit                    6 2014-08-10 00:00:00         2.950000
115. Late Lunch vegetarisch    1107 2017-05-24 00:00:00         2.972674
115. Abendgericht vegetarisch  1209 2017-05-17 00:00:00         2.975972
115. Fleischgericht Abend       511 2013-09-25 00:00:00         2.994814
116. Vital-Linie                 68 2013-09-22 00:00:00         3.019853
116. Late Lunch vegetarisch       1 2019-09-26 00:00:00         3.050000

In [24]:
# select meals of categories with over 100 meals
top_categories = categories[categories['id'] > 100]
pricing_df = df[df['mensa_category'].isin(top_categories.index)].copy()

# create a rolling mean
pricing_df['prices_students_rolling'] = pricing_df.groupby('mensa_category')['prices_students'].transform(lambda x: x.rolling(30).mean())

In [25]:
fig = px.line(pricing_df, 
              x="date", 
              y="prices_students_rolling", 
              hover_name="mensa_category",
              color="mensa_category")
fig.show()

In [27]:
deduped = dedupe_dataframe(df.copy(), ['sname'])

importing data ...
reading from dedupe_dataframe_learned_settings
clustering...
# duplicate sets 483


In [28]:
deduped

id mensa_id        date  \
20      172585      116  2012-09-03   
21      172584      116  2012-09-03   
22      172587      116  2012-09-04   
23      172586      116  2012-09-04   
24      172589      116  2012-09-05   
...        ...      ...         ...   
10366  4859196      115  2020-01-30   
10367  4875009      115  2020-01-30   
10368  4875010      115  2020-01-30   
10369  4893823      115  2020-01-30   
10370  4893824      115  2020-01-30   

                                                    name  \
20     asiatische pilzpfanne mit glasnudeln und sojaw...   
21     gerostete putenbruststreifen turkische art mit...   
22                    hetax-kase paniert mit joghurtdipp   
23     rinderhacksteak spanische art mit oliven und t...   
24                   gerauchertes tofusteak aus asiadipp   
...                                                  ...   
10366  gemuselasagne mit kase uberbacken, dazu salat ...   
10367                         red snapper mit currysauce   
10368  rehbraten hinterlander art mit spatzle und ros...   
10369           herzhaftes paprika-reisfleisch mit salat   
10370  szegediner tofu-gulasch mit krauterkartoffeln ...   

                       category prices_students  \
20           menu 2 vegetarisch            2.85   
21                       menu 1            2.85   
22           menu 2 vegetarisch            2.35   
23                  vital-linie            2.55   
24           menu 2 vegetarisch            2.95   
...                         ...             ...   
10366  abendgericht vegetarisch            2.95   
10367      bistro gourmet fisch            4.85   
10368    bistro gourmet fleisch            5.55   
10369                late lunch            3.05   
10370    late lunch vegetarisch            3.05   

                                                   notes        day  \
20     mit konservierungsstoff, mit geschmacksverstarker     monday   
21                                                           monday   
22                                                          tuesday   
23                                                          tuesday   
24                                                        wednesday   
...                                                  ...        ...   
10366     milch, glutenhaltiges getreide, sellerie, eier   thursday   
10367  mit antioxidationsmittel, senf, glutenhaltiges...   thursday   
10368   glutenhaltiges getreide, soja, eier, wild, milch   thursday   
10369  mit konservierungsstoff, schwefeldioxid und su...   thursday   
10370                glutenhaltiges getreide, senf, soja   thursday   

                                            sname  \
20                          asiatische pilzpfanne   
21     gerostete putenbruststreifen turkische art   
22                             hetax-kase paniert   
23                  rinderhacksteak spanische art   
24                         gerauchertes tofusteak   
...                                           ...   
10366                               gemuselasagne   
10367                                 red snapper   
10368                  rehbraten hinterlander art   
10369              herzhaftes paprika-reisfleisch   
10370                     szegediner tofu-gulasch   

                      mensa_category  cluster id  confidence  
20           116. menu 2 vegetarisch       174.0    0.805628  
21                       116. menu 1       222.0    0.556871  
22           116. menu 2 vegetarisch       267.0    0.767511  
23                  116. vital-linie       233.0    0.722326  
24           116. menu 2 vegetarisch       257.0    0.774813  
...                              ...         ...         ...  
10366  115. abendgericht vegetarisch       258.0    0.610902  
10367      115. bistro gourmet fisch       343.0    0.800295  
10368    115. bistro gourmet fleisch         NaN         NaN  
10369                115. late lunch       290.0    0.805628  
10370    115. late lunch v